In [36]:
%matplotlib inline
import matplotlib.pyplot as plt
from matplotlib.colors import Normalize, SymLogNorm
import numpy as np
from astropy.table import Table, join
from IPython.display import set_matplotlib_formats
from scipy.spatial import distance
import Euclid
import os

set_matplotlib_formats('pdf')
%erun PHZ_NNPZ 0.10.0

from nnpz.reference_sample.ReferenceSample import ReferenceSample
from nnpz.photometry.PhotometryProvider import PhotometryProvider
from nnpz.photometry.SourceIndependantGalacticUnReddening import SourceIndependantGalacticUnReddening

#%erun Phosphoros 0.17
#from PhzCLI.PlotSpecZComparison import SpeczPhotozPlot, displayHistogram, compute_stats

In [95]:
target_catalog_filters = [
#    ('FLUX_U_EXT_LSST_TOTAL', 'FLUXERR_U_EXT_LSST_TOTAL'),
    ('FLUX_G_EXT_LSST_TOTAL', 'FLUXERR_G_EXT_LSST_TOTAL'),
    ('FLUX_R_EXT_LSST_TOTAL', 'FLUXERR_R_EXT_LSST_TOTAL'),
    ('FLUX_I_EXT_LSST_TOTAL', 'FLUXERR_I_EXT_LSST_TOTAL'),
    ('FLUX_Z_EXT_LSST_TOTAL', 'FLUXERR_Z_EXT_LSST_TOTAL'),
    ('FLUX_DETECTION_TOTAL', 'FLUXERR_DETECTION_TOTAL'),
    ('FLUX_Y_TOTAL', 'FLUXERR_Y_TOTAL'),
    ('FLUX_J_TOTAL', 'FLUXERR_J_TOTAL'),
    ('FLUX_H_TOTAL', 'FLUXERR_H_TOTAL')
]
target_fluxes = [f[0] for f in target_catalog_filters]
reference_sample_phot_filters = ['lsst/g', 'lsst/r', 'lsst/i', 'lsst/z', 'euclid/VIS', 'euclid/Y', 'euclid/J', 'euclid/H']
comb = list(zip(np.arange(len(target_catalog_filters)-1), np.arange(1, len(target_catalog_filters))))

In [116]:
mer = Table.read('/home/aalvarez/Downloads/SC8R6/output_mer_cat.fits')
mer = mer[mer['FLUX_DETECTION_TOTAL']/mer['FLUXERR_DETECTION_TOTAL']>=10]
nnpz = Table.read('/home/aalvarez/Downloads/SC8R6/nnpz_output_file.fits', hdu=1)
pdz_bins = Table.read('/home/aalvarez/Downloads/SC8R6/nnpz_output_file.fits', hdu=2)

cat = join(nnpz, mer, 'OBJECT_ID').as_array()
cat_photo = np.zeros((len(cat), len(target_catalog_filters), 2))
for i in range(len(target_catalog_filters)):
    cat_photo[:, i, 0] = cat[target_catalog_filters[i][0]]
    cat_photo[:, i, 1] = cat[target_catalog_filters[i][1]]

In [117]:
ref = ReferenceSample('/home/aalvarez/Downloads/SC8R6/ZReferenceSample/')
ref_photo_prov = PhotometryProvider('/home/aalvarez/Downloads/SC8R6/ZReferenceSample/EUC_PHZ_REFPHOT__20201001T005317.673158Z_00.01.fits')
ref_photo = ref_photo_prov.getData(*reference_sample_phot_filters)
ref_ids = ref_photo_prov.getIds()
idx = np.random.choice(len(ref_photo), 100000)
ref_subset = ref_photo[idx]

INFO    : Found provider PdzProvider
2021-01-14T12:08:20CET ReferenceSample  INFO : Found provider PdzProvider
INFO    : Found provider SedProvider
2021-01-14T12:08:21CET ReferenceSample  INFO : Found provider SedProvider


In [118]:
trans = dict([(k, ref_photo_prov.getFilterTransmission(k)) for k in reference_sample_phot_filters])
dereddener = SourceIndependantGalacticUnReddening(trans, reference_sample_phot_filters)

In [119]:
dereddened = dereddener.de_redden_data(cat_photo, cat['GAL_EBV'])

In [124]:
def plot_nn(obj_id):
    obj = cat[obj_id]
    obj_photo = dereddened[obj_id]
    nn_mask = np.in1d(ref_ids, obj['NEIGHBOR_IDS'])
    nn = ref_photo[nn_mask]
    
    ref_dist = distance.cdist(obj_photo[:,0].reshape(1,-1), ref_subset[:,:,0]).reshape(len(ref_subset))
    nn_dist = distance.cdist(obj_photo[:,0].reshape(1,-1), nn[:,:,0]).reshape(len(nn))
    
    nfilters = len(comb)
    ncols = 2
    nrows = int(np.ceil(nfilters / ncols) + 1)

    fig, axes = plt.subplots(ncols=ncols, nrows=nrows, figsize=(20, 8*nrows))
    for (i, j), ax in zip(comb, axes.ravel()):
        rfx = reference_sample_phot_filters[i]
        rfy = reference_sample_phot_filters[j]

        ax.set_xlabel(rfx)
        ax.set_ylabel(rfy)

        xmin, xmax = min(obj_photo[i,0], nn[:,i,0].min())*0.9, max(obj_photo[i,0], nn[:,i,0].max())*1.1
        ymin, ymax = min(obj_photo[j,0], nn[:,j,0].min())*0.9, max(obj_photo[j,0], nn[:,j,0].max())*1.1
        ax.set_xlim(xmin, xmax)
        ax.set_ylim(ymin, ymax)

        w = ref_dist
        norm = Normalize(vmin=nn_dist.min(), vmax=nn_dist.max()*2)
        
        ref_mask = (ref_subset[:,i,0] >= xmin) & (ref_subset[:,i,0] <= xmax) & (ref_subset[:,j,0] >= ymin) & (ref_subset[:,j,0] <= ymax)
        ax.scatter(ref_subset[ref_mask,i,0], ref_subset[ref_mask,j,0], marker='x', c=w[ref_mask], cmap='coolwarm_r', norm=norm, label='Reference', rasterized=True)

        ss = ax.scatter(nn[:,i,0], nn[:,j,0], marker='D', c=nn_dist, cmap='coolwarm_r', norm=norm, label='Neighbors', rasterized=True)
        
        ax.errorbar([obj_photo[i,0]], [obj_photo[j,0]], xerr=[obj_photo[i,1]], yerr=[obj_photo[j,1]], marker='o', color='red', label=f'Target {obj_id}')
        ax.scatter([obj[f'{rfx}_MEAN']], [obj[f'{rfy}_MEAN']], marker='X', color='green', label='Mean photometry')
        
        plt.colorbar(ss, ax=ax, label='Euclidean Distance')
        ax.legend()
        
    axes[-1, 0].plot(pdz_bins, obj['REDSHIFT_PDF'])
    axes[-1, 0].set_title('PDZ')
    
    for n in ref_ids[nn_mask]:
        pdz = ref.getPdzData(n)
        axes[-1, 1].plot(pdz[:,0], pdz[:,1])
    axes[-1, 1].set_title('Neighbor PDZ')
    
    plt.tight_layout()

In [125]:
plot_nn(125)

<Figure size 1440x2880 with 17 Axes>

In [122]:
plot_nn(904)

<Figure size 1440x2880 with 17 Axes>

In [123]:
plot_nn(2048)

<Figure size 1440x2880 with 17 Axes>

In [64]:
plot_nn(32)

<Figure size 1440x2880 with 17 Axes>

In [31]:
withz = Table.read('/home/aalvarez/Downloads/SC8R6/ZReferenceSample/RefWithZ.fits')

In [94]:
fig, axes = plt.subplots(ncols=2, figsize=(12, 6))
bins = axes[0].hist(cat['REDSHIFT_MEDIAN'], bins=20)
axes[1].hist(withz['Z_OBS'], bins=bins[1])
plt.show()

<Figure size 864x432 with 2 Axes>